In [23]:
import requests
import pandas as pd
from pyquery import PyQuery as pq

url = "http://www.krasnodar.vybory.izbirkom.ru/region/krasnodar?action=ikTree&region=23&vrn="
vrn_committe_in_krasnodar = '22320001989385'
url_get_UIK = "&onlyChildren=true&id="

headers = requests.utils.default_headers()
headers.update({ 'User-Agent': 'Mozilla/5.0 (X11; Ubuntu; Linux x86_64; rv:52.0) Gecko/20100101 Firefox/69.0'})

# получим id ТИК
resp = requests.get(url + vrn_committe_in_krasnodar , headers)
id_TIK = [i['id'] for i in resp.json()[0]['children']]

# совместим ТИК и данные о УИК
id_UIK, TIK_and_UIK = [], []
for i in id_TIK:
    resp = requests.get(url + i + url_get_UIK + i, headers)
    TIK_and_UIK.append({i:resp.json()})
    id_UIK += [i['id'] for i in resp.json()]
    

print(TIK_and_UIK)


[{'4234018213637': [{'id': '4234018274986', 'text': 'Участковая избирательная комиссия №2001', 'state': {'opened': False, 'selected': False}, 'children': False}, {'id': '4234018274988', 'text': 'Участковая избирательная комиссия №2002', 'state': {'opened': False, 'selected': False}, 'children': False}, {'id': '4234018274990', 'text': 'Участковая избирательная комиссия №2003', 'state': {'opened': False, 'selected': False}, 'children': False}, {'id': '4234018274992', 'text': 'Участковая избирательная комиссия №2004', 'state': {'opened': False, 'selected': False}, 'children': False}, {'id': '4234018274994', 'text': 'Участковая избирательная комиссия №2005', 'state': {'opened': False, 'selected': False}, 'children': False}, {'id': '4234018274996', 'text': 'Участковая избирательная комиссия №2006', 'state': {'opened': False, 'selected': False}, 'children': False}, {'id': '4234018274998', 'text': 'Участковая избирательная комиссия №2007', 'state': {'opened': False, 'selected': False}, 'child

In [3]:
# получим список челонов комисси в каждом УИК
from bs4 import BeautifulSoup
from threading import Thread

def parse_info_about_committeemans(*id_UIK):
    url_get_committeemans = "http://www.krasnodar.vybory.izbirkom.ru/region/krasnodar?action=ik&vrn="
    global dfs
    for i in id_UIK:
        resp = requests.get(url_get_committeemans + i, headers)
        html_text = BeautifulSoup(resp.text, 'html')
        table_text = html_text.find_all('table')
        dfs.append({i:pd.read_html(str(table_text[-1]))})
    return dfs

arg1 = id_UIK[:1000]
arg2 = id_UIK[1000:2000]
arg3 = id_UIK[2000:]
dfs = []

thread1 = Thread(target=parse_info_about_committeemans, args=arg1)
thread2 = Thread(target=parse_info_about_committeemans, args=arg2)
thread3 = Thread(target=parse_info_about_committeemans, args=arg3)
thread1.start()
thread2.start()
thread3.start()
thread1.join()
thread2.join()
thread3.join()


print(dfs)








[{'4234006201920': [   Unnamed: 0                              ФИО            Статус  \
0           1  Анистратенко Жанна Вячеславовна      Председатель   
1           2        Якуба Наталья Геннадьевна  Зам.председателя   
2           3    Кутнякова Ирина Александровна         Секретарь   
3           4         Лютый Александр Иванович              Член   
4           5   Петрушенко Надежда Анатольевна              Член   
5           6     Савенко Александр Николаевич              Член   
6           7        Харченко Татьяна Ивановна              Член   

                     Кем предложен в состав комиссии  
0               собрание избирателей по месту работы  
1           собрание избирателей по месту жительства  
2           собрание избирателей по месту жительства  
3  Краснодарское региональное отделение Политичес...  
4           собрание избирателей по месту жительства  
5  Брюховецкое районное отделение Краснодарского ...  
6  Региональное отделение в Краснодарском крае По.

In [4]:
# получим список всех кандидатов из Единого округа и отсеем кандидатов из КПРФ

url_candidate = "http://cikrf.ru/iservices/sgo-visual-rest/vibory/4234220141768/candidates?page="

all_page = 18 
candidats = []
for page in range(1,all_page+1):
    resp = requests.get(url_candidate + str(page) , headers)
    candidats +=[i for i in resp.json()["_embedded"]["candidateDtoList"]]

for i in range(len(candidats)):
    df_candidate = pd.DataFrame(candidats)

KPRF_candidate = df_candidate.loc[df_candidate['namio'] == 'Краснодарское краевое отделение политической партии "КОММУНИСТИЧЕСКАЯ ПАРТИЯ РОССИЙСКОЙ ФЕДЕРАЦИИ"']
print(KPRF_candidate)


    index            vrn                              fio  \
0       1  4234220142844        Азаров Игорь Владимирович   
1       8  4234220143645        Востриков Алексей Никитич   
2      22  4234220144088            Кунда Олег Викторович   
3      36  4234220142837      Шибалкин Игорь Владимирович   
39      2  4234220145147     Андреев Евгений Владимирович   
40      3  4234220143521        Богайчук Сергей Сергеевич   
41      4  4234220143514           Брохес Юрий Михайлович   
42      5  4234220144170         Бурцев Сергей Евгеньевич   
43      6  4234220143792   Валявский Александр Викторович   
44      7  4234220142831  Вергелес Александр Вячеславович   
45      9  4234220144156          Гирич Владимир Иванович   
46     10  4234220143299     Голубков Павел Александрович   
47     11  4234220145454       Грачевская Илона Сергеевна   
48     12  4234220142912        Дубенко Юрий Владимирович   
49     13  4234220144111      Иванов Александр Георгиевич   
50     14  4234220147054

In [20]:
# поиск номера УИК, где представители КПРФ были в членах жюри
names_KPRF_candidate = KPRF_candidate["fio"]
id_UIK_with_KPRF_candidate = []

for name in names_KPRF_candidate: 
    for num in range(len(dfs)):
        key = next(iter(dfs[num].keys()))
        if dfs[num][key][0]['ФИО'].str.contains(pat = name, regex=False, case=True, na=False).any():
            id_UIK_with_KPRF_candidate.append(key)
    
print(id_UIK_with_KPRF_candidate)





['4234020369154', '4234060106523']


Из всего списка УИК по Краснодарскому краю найдены только два участка, членами комиссий которых были представители КПРФ. Следовательно, в остальных участках представители КПРФ в составе не было. Надем номера этих участков.

In [42]:
# получим список УИК, где нет членов КПРФ в списке
id_UIK_not_KPRF_candidats = list(set(id_UIK) - set(id_UIK_with_KPRF_candidate))
#print(id_UIK_not_KPRF_candidats)

numbers_UIK = []

for num in range(len(TIK_and_UIK)):
    key_tik = next(iter(TIK_and_UIK[num].keys()))
    for i in range(len(TIK_and_UIK[num][key_tik])):
        if TIK_and_UIK[num][key_tik][i]['id'] in id_UIK_not_KPRF_candidats:
            numbers_UIK.append(TIK_and_UIK[num][key_tik][i]['text'].split('№')[1])
print(numbers_UIK)
            
        


['2001', '2002', '2003', '2004', '2005', '2006', '2007', '2008', '2009', '2010', '2011', '2012', '2013', '2014', '2015', '2016', '2017', '2018', '2019', '2020', '2021', '2022', '2023', '2024', '2025', '2026', '2027', '2028', '2029', '2030', '2031', '2032', '2033', '2034', '2035', '2036', '2037', '2038', '2039', '2040', '2041', '2042', '2043', '2044', '2045', '2046', '2047', '2048', '2049', '2050', '2051', '2052', '2053', '2054', '2055', '2056', '2057', '2058', '2059', '2060', '2061', '6001', '6002', '6003', '6004', '6005', '6006', '6007', '6009', '6010', '6011', '6012', '6013', '6014', '6015', '6016', '6017', '6018', '6019', '6020', '6021', '6022', '6023', '6024', '6025', '6026', '6027', '6028', '6029', '6030', '6031', '6032', '6033', '6034', '6035', '6036', '6037', '6038', '6039', '6040', '6041', '6042', '6043', '6044', '6045', '6046', '6047', '6048', '6049', '6050', '6051', '6052', '6053', '6054', '6055', '6056', '6057', '6058', '6059', '6060', '6061', '6062', '6063', '6064', '6065',